## 機器學習 HW1 Data Preprocessing (bankruptcy.csv)

- 學號: 311706017
- 姓名: 陳詩婷



### Dataset:  

這一份檔案主要做bankruptcy.csv的前處理，此資料集的特徵共有95個特徵
- Bankrupt? 為預測目標(label)


In [46]:
import pandas as pd
df = pd.read_csv('bankruptcy.csv')  #匯入資料，告訴pd.read_csv要匯入的檔案的路徑，這邊我把檔案和ipynb放在同一目錄之下
df

Unnamed: 0  Bankrupt?  \
0              0          1   
1              1          1   
2              2          1   
3              3          1   
4              4          1   
...          ...        ...   
6814        6814          0   
6815        6815          0   
6816        6816          0   
6817        6817          0   
6818        6818          0   

       ROA(C) before interest and depreciation before interest  \
0                                              0.370594          
1                                              0.464291          
2                                              0.426071          
3                                              0.399844          
4                                              0.465022          
...                                                 ...          
6814                                           0.493687          
6815                                           0.475162          
6816                                           0.472725          
6817                                           0.506264          
6818                                           0.493053          

       ROA(A) before interest and % after tax  \
0                                    0.424389   
1                                    0.538214   
2                                    0.499019   
3                                    0.451265   
4                                    0.538432   
...                                       ...   
6814                                 0.539468   
6815                                 0.538269   
6816                                 0.533744   
6817                                 0.559911   
6818                                 0.570105   

       ROA(B) before interest and depreciation after tax  \
0                                              0.405750    
1                                              0.516730    
2                                              0.472295    
3                                              0.457733    
4                                              0.522298    
...                                                 ...    
6814                                           0.543230    
6815                                           0.524172    
6816                                           0.520638    
6817                                           0.554045    
6818                                           0.549548    

       Operating Gross Margin   Realized Sales Gross Margin  \
0                    0.601457                      0.601457   
1                    0.610235                      0.610235   
2                    0.601450                      0.601364   
3                    0.583541                      0.583541   
4                    0.598783                      0.598783   
...                       ...                           ...   
6814                 0.604455                      0.604462   
6815                 0.598308                      0.598308   
6816                 0.610444                      0.610213   
6817                 0.607850                      0.607850   
6818                 0.627409                      0.627409   

       Operating Profit Rate   Pre-tax net Interest Rate  \
0                   0.998969                    0.796887   
1                   0.998946                    0.797380   
2                   0.998857                    0.796403   
3                   0.998700                    0.796967   
4                   0.998973                    0.797366   
...                      ...                         ...   
6814                0.998992                    0.797409   
6815                0.998992                    0.797414   
6816                0.998984                    0.797401   
6817                0.999074                    0.797500   
6818                0.998080                    0.801987   

       After-tax net Interest Rate  ...   Net Income

- 資料量: 6819
- 特徵數:95
- 可以發現空值會顯示NaN，所以下一步就需要填補空值

特徵的資料型態都是數值

In [61]:
#因為特徵太多，更改jupyter預設的顯示方式，這樣就能完整瀏覽資料表
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', -1)

/tmp/ipykernel_700658/3462665596.py:4: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('display.max_colwidth', -1)


In [34]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6819 entries, 0 to 6818
Data columns (total 97 columns):
 #   Column                                                    Non-Null Count  Dtype  
---  ------                                                    --------------  -----  
 0   Unnamed: 0                                                6819 non-null   int64  
 1   Bankrupt?                                                 6819 non-null   int64  
 2    ROA(C) before interest and depreciation before interest  6721 non-null   float64
 3    ROA(A) before interest and % after tax                   6719 non-null   float64
 4    ROA(B) before interest and depreciation after tax        6721 non-null   float64
 5    Operating Gross Margin                                   6719 non-null   float64
 6    Realized Sales Gross Margin                              6721 non-null   float64
 7    Operating Profit Rate                                    6719 non-null   float64
 8    Pre-tax net Inter

<hr/>

### 前處理步驟: 
1) 觀察資料分布，填補空值

2) 處理類別不平衡問題 

3) Feature Selection 

4) 存檔，作業需繳交 .xlsx 下一次要用到 .csv 

<hr/>

# 1. 填補空值

### 1-1. 刪除無法填補的資料

檢查每一個特徵是否有缺失值，發現有缺失值

In [35]:
df.isnull().sum()  

Unnamed: 0                                                    0
Bankrupt?                                                     0
 ROA(C) before interest and depreciation before interest     98
 ROA(A) before interest and % after tax                     100
 ROA(B) before interest and depreciation after tax           98
                                                           ... 
 Liability to Equity                                        100
 Degree of Financial Leverage (DFL)                          99
 Interest Coverage Ratio (Interest expense to EBIT)          99
 Net Income Flag                                            100
 Equity to Liability                                        100
Length: 97, dtype: int64

為避免資料失真，刪去缺失過多特徵的資料，這裡設門檻為0.2，共有10個特徵故超過2個特徵的欄位為空就移除該筆資料

In [47]:
def drop_nan_checking(df, thrshold):  # 參數: 資料, 判斷該筆資料去留的門檻值
       
    drop_row = []
    for row in range(len(df)):  # 前兩行是index

        nullCount = df.loc[row].isnull().sum() / 10  # 計算特徵的缺失比例，若高於我們預設的門檻就較失真 --> 刪除這筆資料 (應該可以不要寫死)
        if nullCount > thrshold:
            drop_row.append(row)
    return drop_row


drop_row = drop_nan_checking(df, 0.2)
df.drop(drop_row, axis=0,inplace=True)     
#print("drop: ", drop_row)

### 1-2. 填補資料

以平均值填補填補數值型態資料

In [48]:
#如果欄位有出現空值(且該筆資料缺少的特徵少於二成)，就進行填補

df.fillna(df.mean(), inplace=True) #其實是不用迴圈就全部填好了  

重新觀察資料，檢查是否仍有空值

In [49]:
df.isnull().sum()  

Unnamed: 0                                                  0
Bankrupt?                                                   0
 ROA(C) before interest and depreciation before interest    0
 ROA(A) before interest and % after tax                     0
 ROA(B) before interest and depreciation after tax          0
                                                           ..
 Liability to Equity                                        0
 Degree of Financial Leverage (DFL)                         0
 Interest Coverage Ratio (Interest expense to EBIT)         0
 Net Income Flag                                            0
 Equity to Liability                                        0
Length: 97, dtype: int64

<hr/>

# 2. 類平衡
- 在分類問題中，若是要預測的label本身存在不平衡的問題，將造成model有較高的bias，為了使model更泛化，需要使各類別比例相近
- 例如過去出現的AI歧視議題，就與dataset本身有較多黑人犯罪的資料標籤有關，或是腫瘤辨識模型類不平衡而使判斷結果有較高的偽陰性

### 2a. 隨機取樣

目的是讓大類與小類的資料量差距減少，使模型更泛化
- 資料量變化: 5712 => 4569

In [51]:
import math

persent = math.floor(len(df.index) * 0.8)
# print(persent)
df_rd = df.sample(persent)

### 2b. SMOTEENN
- Over sampling: 目的是讓小類的資料量可以增加，接近大類的資料量(SMOTE)
- Under sampling: 減少大類的抽樣數，達成類平衡(ENN)
- 資料量變化: 4569 =>7884

In [76]:
# https://imbalanced-learn.org/stable/references/generated/imblearn.combine.SMOTEENN.html?highlight=ee#imblearn.combine.SMOTEENN

from collections import Counter
from sklearn.datasets import make_classification
from imblearn.combine import SMOTEENN

#---------------------------------------------------
X = df_rd.drop(['Bankrupt?'], axis=1) # feature
y = df_rd["Bankrupt?"] # label
print('Original dataset shape %s' % Counter(y))

#---------------------------------------------------
sme = SMOTEENN(random_state=42)
X_res, y_res = sme.fit_resample(X, y)
df_smoteenn = pd.concat([X_res, y_res], axis=1, join='inner')
print('Resampled dataset shape %s' % Counter(y_res))

Original dataset shape Counter({0: 4416, 1: 153})
Resampled dataset shape Counter({1: 4201, 0: 3683})


In [44]:
''' #delete
#pip install imbalanced-learn
from imblearn.over_sampling import SMOTE

#df['Bankrupt?']
y = df['Bankrupt?'] # 預測用的label
X = df.pop('Bankrupt?') # 預測用的label

sm = SMOTE(random_state = 0)
'''

# 3. 特徵選取
- 模型在訓練時採用太多特徵會增加運算的負擔，也可能讓模型overfitting而不泛化，因此需要做特徵選取

### 3a. Filter
- 透過Pearson 相關係數，觀察X對於Y是否顯著
- 由於下一步要做的逐步回歸是相當耗能的，先以filter排除「與label相關性過低的特徵」
- 若特徵之間具共線性，擇一即可


In [64]:
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt


featuresCorr = df.corr()
featuresCorr

Unnamed: 0  \
Unnamed: 0                                                1.000000     
Bankrupt?                                                -0.097391     
 ROA(C) before interest and depreciation before interest  0.121885     
 ROA(A) before interest and % after tax                   0.109322     
 ROA(B) before interest and depreciation after tax        0.115037     
 Operating Gross Margin                                   0.078157     
 Realized Sales Gross Margin                              0.078842     
 Operating Profit Rate                                   -0.005768     
 Pre-tax net Interest Rate                               -0.002158     
 After-tax net Interest Rate                             -0.000312     
 Non-industry income and expenditure/revenue              0.011523     
 Continuous interest rate (after tax)                    -0.000765     
 Operating Expense Rate                                  -0.032583     
 Research and development expense rate                    0.165448     
 Cash flow rate                                           0.055706     
 Interest-bearing debt interest rate                      0.065668     
 Tax rate (A)                                             0.026939     
 Net Value Per Share (B)                                  0.192152     
 Net Value Per Share (A)                                  0.185993     
 Net Value Per Share (C)                                  0.183375     
 Persistent EPS in the Last Four Seasons                  0.158131     
 Cash Flow Per Share                                      0.086727     
 Revenue Per Share (Yuan ¥)                              -0.003961     
 Operating Profit Per Share (Yuan ¥)                      0.126705     
 Per Share Net profit before tax (Yuan ¥)                 0.145076     
 Realized Sales Gross Profit Growth Rate                 -0.014067     
 Operating Profit Growth Rate                            -0.006128     
 After-tax Net Profit Growth Rate                         0.007647     
 Regular Net Profit Growth Rate                           0.007040     
 Continuous Net Profit Growth Rate                        0.018646     
 Total Asset Growth Rate                                 -0.017384     
 Net Value Growth Rate                                   -0.006333     
 Total Asset Return Growth Rate Ratio                     0.000544     
 Cash Reinvestment %                                      0.053369     
 Current Ratio                                           -0.006159     
 Quick Ratio                                             -0.021705     
 Interest Expense Ratio                                  -0.031618     
 Total debt/Total net worth                              -0.002763     
 Debt ratio %                                            -0.126435     
 Net worth/Assets                                         0.126568     
 Long-term fund suitability ratio (A)                     0.043983     
 Borrowing dependency                                    -0.071136     
 Contingent liabilities/Net worth                        -0.006985     
 Operating profit/Paid-in capital                         0.126259     
 Net profit before tax/Paid-in capital                    0.154879     
 Inventory and accounts receivable/Net value             -0.019403     
 Total Asset Turnover                                     0.109623     
 Accounts Receivable Turnover                            -0.019156     
 Average Collection Days                                 -0.003557     
 Inventory Turnover Rate (times)                         -0.130988     
 Fixed Assets Turnover Frequency                         -0.122879     
 Net Worth Turnover Rate (times)                          0.036480     
 Revenue per person                                      -0.004323     
 Operating profit per person                              0.004813     
 Allocation rate per person                               0.015473     
 Working Capital to Total 

僅保留特徵與label之相關係數大於正負0.1的(共有30個):

- Liability to Equity
- <b>Net Income to Stockholder's Equity</b>
- Net Income to Total Assets
- <b>Liability-Assets Flag</b>
- <b>Current Liability to Current Assets</b>
- CFO to Assets
- Current Liability to Equity
- Equity to Long-term Liability
- Total expense/Assets
- Retained Earnings to Total Assets
- Current Liabilities/Equity
- Working Capital/Equity
- Current Liability to Assets
- Working Capital to Total Assets
- Operating profit/Paid-in capital
- <b>Net profit before tax/Paid-in capital</b>
- Operating profit/Paid-in capital
- Borrowing dependency
- Net worth/Assets
- Debt ratio %
- <b>Operating Profit Per Share (Yuan ¥)</b>
- Per Share Net profit before tax (Yuan ¥)
- <b>Tax rate (A)</b>
- <b>Net Value Per Share (B)</b>
- <b>Net Value Per Share (A)</b>
- <b>Net Value Per Share (C)</b>
- Persistent EPS in the Last Four Seasons
- ROA(C) before interest and depreciation before interest
- <b>ROA(A) before interest and % after tax</b>
- ROA(B) before interest and depreciation after tax



In [82]:
# 僅保留30個特徵做逐步回歸，降低運算負擔
cor_feature = [' Liability to Equity',' Net Income to Stockholder\'s Equity',' Net Income to Total Assets',' Liability-Assets Flag',' Current Liability to Current Assets',' CFO to Assets',' Current Liability to Equity',' Equity to Long-term Liability',' Total expense/Assets',' Retained Earnings to Total Assets',' Current Liabilities/Equity',' Working Capital/Equity',' Current Liability to Assets',' Working Capital to Total Assets',' Operating profit/Paid-in capital',' Net profit before tax/Paid-in capital',' Operating profit/Paid-in capital',' Borrowing dependency',' Net worth/Assets',' Debt ratio %',' Operating Profit Per Share (Yuan ¥)',' Per Share Net profit before tax (Yuan ¥)',' Tax rate (A)',' Net Value Per Share (B)',' Net Value Per Share (A)',' Net Value Per Share (C)',' Persistent EPS in the Last Four Seasons',' ROA(C) before interest and depreciation before interest',' ROA(A) before interest and % after tax',' ROA(B) before interest and depreciation after tax']

### 3b. wrapper
- 使用逐步回歸(stepwise)
- 逐一排除特徵，排除與y相關性不高的特徵，找出最適合預測y的特徵子集合
- <b>這邊設定僅保留10個特徵</b>


In [72]:
from sklearn.feature_selection import SequentialFeatureSelector
from sklearn.neighbors import KNeighborsClassifier
# https://towardsdatascience.com/stepwise-regression-tutorial-in-python-ebf7c782c922


X = df[cor_feature] # feature
y = df["Bankrupt?"] # label
knn = KNeighborsClassifier(n_neighbors=3)
sfs = SequentialFeatureSelector(knn, n_features_to_select=10)
sfs.fit(X, y)

SequentialFeatureSelector(estimator=KNeighborsClassifier(n_neighbors=3),
                          n_features_to_select=10)

In [73]:
sfs.get_support()

array([False,  True, False,  True,  True, False, False, False, False,
       False, False, False, False, False, False,  True, False, False,
       False, False,  True, False,  True,  True,  True,  True, False,
       False,  True, False])

In [84]:
col = ['Bankrupt?', ' Net Income to Stockholder\'s Equity',' Liability-Assets Flag',' Current Liability to Current Assets',' Net profit before tax/Paid-in capital',' Operating Profit Per Share (Yuan ¥)',' Tax rate (A)',' Net Value Per Share (B)',' Net Value Per Share (A)',' Net Value Per Share (C)',' ROA(A) before interest and % after tax']
          # label         # feature
df_cleaned = df_smoteenn[col]

## 前處理後的特徵量與資料量
- row: 資料量
- column: 特徵量

In [85]:
df_cleaned

Bankrupt?   Net Income to Stockholder's Equity   Liability-Assets Flag  \
0     0          0.838057                             0.000000                 
1     0          0.840082                             0.000000                 
2     0          0.844581                             0.000000                 
3     0          0.843794                             0.000000                 
4     0          0.840916                             0.000000                 
5     0          0.843107                             0.000000                 
6     0          0.842245                             0.000000                 
7     0          0.839704                             0.000000                 
8     0          0.841340                             0.000000                 
9     0          0.840527                             0.000000                 
10    0          0.841576                             0.000000                 
11    0          0.840112                             0.000000                 
12    0          0.844417                             0.000000                 
13    0          0.841222                             0.000000                 
14    0          0.837382                             0.000000                 
15    0          0.840688                             0.000000                 
16    0          0.841111                             0.000000                 
17    0          0.839239                             0.000000                 
18    0          0.841057                             0.000000                 
19    0          0.840401                             0.000000                 
20    0          0.841180                             0.000000                 
21    0          0.839414                             0.000000                 
22    0          0.840132                             0.000000                 
23    0          0.843320                             0.000000                 
24    0          0.848340                             0.000000                 
25    0          0.839168                             0.000000                 
26    0          0.840362                             0.001240                 
27    0          0.842550                             0.000000                 
28    0          0.840518                             0.000000                 
29    0          0.844435                             0.000000                 
30    0          0.844910                             0.000000                 
31    0          0.843245                             0.000000                 
32    0          0.839483                             0.000000                 
33    0          0.841904                             0.000000                 
34    0          0.839482                             0.000000                 
35    0          0.841754                             0.000000                 
36    0          0.843637                             0.000000                 
37    0          0.840046                             0.000000                 
38    0          0.842224                             0.000000                 
39    0          0.844676                             0.000000                 
40    0          0.841662                             0.000000                 
41    0          0.843263                             0.000000                 
42    0          0.842406                             0.000000                 
43    0          0.840777                             0.000000                 
44    0          0.841818                             0.000000                 
45    0          0.834971                             0.000000                 
46    0          0.842475                             0.000000                 
47    0          0.840278                             0.000000                 
48    0          0.840578                             0.000000                 
49    

經過前處理之後

- 資料量: 7884
- 特徵數: 95 => 10

## 匯出處理好的資料

In [86]:
df.to_excel('bank_clean.xlsx') 
df.to_csv('bank_clean.csv') 

## 作業要求

1) A brief report logically describes the algorithm, method, or thinking applied to address the above issues using PDF format.

2) Excel files.

3) Code: Please submit a PDF file and a source code with py. or .ipynb format.